In [3]:
%pip install -qU pypdf

Note: you may need to restart the kernel to use updated packages.


You should consider upgrading via the 'e:\Programming-Projects\Hackathon\hackrx6\venv\Scripts\python.exe -m pip install --upgrade pip' command.


In [1]:
from langchain_community.document_loaders import PyPDFLoader
from langchain_community.vectorstores import FAISS

In [14]:
# file_path = "docs/BAJHLIP23020V012223.pdf"
file_path = "docs/042f627c5d8f619cf62cc21f864b08dfd59059d0b9aab805d132e0014489d625.pdf"

In [15]:
loader = PyPDFLoader(file_path)
pages = []
async for page in loader.alazy_load():
    pages.append(page)

In [7]:
len(pages)

49

In [8]:
pages[0].page_content

'UIN- BAJHLIP23020V012223                                 Global Health Care/ Policy Wordings/Page 1 \n \n \nBajaj Allianz General Insurance Co. Ltd.                       \nBajaj Allianz House, Airport Road, Yerawada, Pune - 411 006. Reg. No.: 113 \nFor more details, log on to: www.bajajallianz.com | E-mail: bagichelp@bajajallianz.co.in or \nCall at: Sales - 1800 209 0144 / Service - 1800 209 5858 (Toll Free No.) \nIssuing Office: \n \nGLOBAL HEALTH CARE \n \n \nPolicy Wordings \n \nUIN- BAJHLIP23020V012223 \nSECTION A) PREAMBLE \n \nWhereas the Insured described in the Policy Schedule hereto (hereinafter called the ‘Insured’  or “Policyholder” or \n“Insured Person”) has made to Bajaj Allianz General Insurance Company Limited (hereinafter called the “Company” \nor “Insurer” or “Insurance Company”) a proposal or Proposal as mentioned in the transcript of the Proposal, which \nshall be the basis of this Contract and is deemed to be incorporated herein, containing certain undertakings , 

In [19]:
len(pages[0].page_content)

4500

In [16]:
# Splitting into chunks
from langchain_text_splitters import RecursiveCharacterTextSplitter
text_splitter = RecursiveCharacterTextSplitter(chunk_size=1000, chunk_overlap=200)
splits = text_splitter.split_documents(pages)

In [28]:
len(splits[0].page_content)

978

In [3]:
# Embeddings
from langchain_huggingface import HuggingFaceEmbeddings
# all_mini_embeddings = HuggingFaceEmbeddings(model_name="all-MiniLM-L6-v2")
bge_embeddings = HuggingFaceEmbeddings(model_name="BAAI/bge-small-en-v1.5")

e:\Programming-Projects\Hackathon\hackrx6\venv\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [4]:
embeddings = bge_embeddings
vector_store = FAISS.from_documents(splits, embedding=embeddings)

NameError: name 'splits' is not defined

In [5]:
# Store the vector DB locally
vector_store.save_local("vector_store/faiss_index_bajaj")

NameError: name 'vector_store' is not defined

In [13]:
# Load the saved vector store
# vector_store = FAISS.load_local("vector_store/faiss_index_bajaj", embeddings, allow_dangerous_deserialization=True)
vector_store = FAISS.load_local("vector_store/042f627c5d8f619cf62cc21f864b08dfd59059d0b9aab805d132e0014489d625", embeddings, allow_dangerous_deserialization=True)

In [7]:
retriever = vector_store.as_retriever()

In [38]:
from dotenv import load_dotenv
from langchain_google_genai import ChatGoogleGenerativeAI

load_dotenv()

llm = ChatGoogleGenerativeAI(
    model="gemini-2.0-flash",
    temperature=0,
    max_tokens=None,
    timeout=None,
    max_retries=2,
)

In [ ]:
from langchain_core.runnables import RunnableLambda

def log_chunks(docs):
    print("\nRetrieved Chunks:\n" + "\n---\n".join(doc.page_content for doc in docs))
    return docs

# Modified retriever pipeline
logged_retriever = retriever | RunnableLambda(log_chunks) | format_docs

In [56]:
from langchain_core.output_parsers import StrOutputParser
from langchain_core.runnables import RunnablePassthrough
from langchain import hub


prompt = hub.pull("rlm/rag-prompt")

# Post-processing
def format_docs(docs):
    return "\n\n".join(doc.page_content for doc in docs)

# Chain
rag_chain = (
    {"context": logged_retriever, "question": RunnablePassthrough()}
    | prompt
    | llm
    | StrOutputParser()
)

# Question
# rag_chain.invoke("what is the minimum and maximum In-patient Hospitalization Treatment Limits for Imperial plus plan?")
# rag_chain.invoke("46-year-old male, knee surgery in Pune, 3-month-old insurance policy")
rag_chain.invoke("knee surgery?")


🔍 Retrieved Chunks:
75  Rotational Arc Therapy 275  Testicular biopsy  
76   Tele gamma therapy 276  laparoscopic cardiomyotomy( Hellers) 
77  FSRT-Fractionated SRT 277  Sentinel node biopsy malignant melanoma 
78  VMAT-Volumetric Modulated Arc Therapy 278   laparoscopic pyloromyotomy( Ramstedt) 
79  SBRT-Stereotactic Body Radiotherapy Orthopedics 
80  Helical Tomotherapy 279  Arthroscopic Repair of ACL tear knee 
81  SRS-Stereotactic Radiosurgery 280  Closed reduction of minor Fractures 
82  X-Knife SRS 281  Arthroscopic repair of PCL tear knee 
83  Gammaknife SRS 282  Tendon shortening 
84  TBI- Total Body Radiotherapy 283  Arthroscopic  Meniscectomy - Knee 
85  intraluminal Brachytherapy 284  Treatment of clavicle dislocation 
86   Electron Therapy 285  Arthroscopic meniscus repair 
87  TSET-Total Electron Skin Therapy 286  Haemarthrosis knee- lavage 
88  Extracorporeal Irradiation of  Blood Products 287  Abscess  knee joint drainage  
89  Telecobalt Therapy 288  Carpal tunnel rele

'Knee surgeries include arthroscopic repair of ACL or PCL tears, arthroscopic meniscectomy or meniscus repair, haemarthrosis knee lavage, abscess knee joint drainage, and repair of the knee cap tendon. Other knee surgeries are fixation, repair of the knee joint, and removal of the knee cap bursa.'

In [9]:
# chunks = retriever.invoke("What is the grace period for premium payment under the National Parivar Mediclaim Plus Policy?")
chunks = retriever.invoke("grace period")

for chunk in chunks:
    print(chunk.page_content)
    print("------------------------------")

ii. the patient takes treatment at home on account of non availability of bed/ room in a hospital.
2.19 Family members means spouse, children and parents of the insured, covered by the Policy.
2.20 Floater Sum Insured means the sum insured, as mentioned in the Schedule, available to all the insured persons, for any and
all claims made in the aggregate during each policy year.
2.21 Grace Period means the specified period of time, immediately following the premium due date during which premium
payment can be made to renew or continue a policy in force without loss of continuity benefits pertaining to Waiting Periods
and coverage of Pre-Existing Diseases. The Grace Period for payment of the premium shall be thirty days.
Coverage shall not be available during the period for which no premium is received.
2.22Hospital means any institution established for in-patient care and day care treatment of disease/ injuries and which has been
------------------------------
5.22 Free Look Period
The Fr

In [ ]:
chunks = retriever.invoke("What is the grace period for premium payment under the National Parivar Mediclaim Plus Policy?")
# chunks = retriever.invoke("grace period")

for chunk in chunks:
    print(chunk.page_content)
    print("------------------------------")

ii. the patient takes treatment at home on account of non availability of bed/ room in a hospital.
2.19 Family members means spouse, children and parents of the insured, covered by the Policy.
2.20 Floater Sum Insured means the sum insured, as mentioned in the Schedule, available to all the insured persons, for any and
all claims made in the aggregate during each policy year.
2.21 Grace Period means the specified period of time, immediately following the premium due date during which premium
payment can be made to renew or continue a policy in force without loss of continuity benefits pertaining to Waiting Periods
and coverage of Pre-Existing Diseases. The Grace Period for payment of the premium shall be thirty days.
Coverage shall not be available during the period for which no premium is received.
2.22Hospital means any institution established for in-patient care and day care treatment of disease/ injuries and which has been
------------------------------
5.5.8 Optional Co-payment
Th

In [20]:
from langchain.retrievers import EnsembleRetriever
from langchain.retrievers import BM25Retriever

semantic_retriever = vector_store.as_retriever(search_kwargs={"k": 5})
bm25_retriever = BM25Retriever.from_documents(splits)
bm25_retriever.k = 5

retriever = EnsembleRetriever(
    retrievers=[semantic_retriever, bm25_retriever],
    weights=[0.3, 0.7]
)

In [22]:
query = "What is the grace period for premium payment"
chunks = retriever.get_relevant_documents(query)

for i, chunk in enumerate(chunks):
    print(f"\n--- Chunk {i+1} ---\n{chunk.page_content}")


--- Chunk 1 ---
Medicine/ Central Council for Homeopathy; or 
c. AYUSH Hospital, standalone or co-located with in-patient healthcare facility of any recognized system of medicine, 
registered with the local authorities, wherever applicable, and is under the supervision of a qualified registered 
AYUSH Medical Practitioner and must comply with all the following criterion:  
i. Having at least 5 in-patient beds; 
ii. Having qualified AYUSH Medical Practitioner in charge round the clock; 
iii. Having dedicated AYUSH therapy sections as required;  
iv. Maintaining daily records of the patients and making them accessible to the insurance company’s authorized 
representative 
 
2.8 Break in policy means the period of gap that occurs at the end of the existing Policy Period due date, when the premium due 
for renewal on a given policy or instalment premium due is not paid on or before the premium renewal date or grace period.

--- Chunk 2 ---
2.19  Family members means spouse, children and p

In [23]:
hypothetical_answer = "The grace period for premium payment under most health insurance policies, including the National Parivar Mediclaim Plus Policy, is typically 15 to 30 days. This allows policyholders to make payments after the due date without losing coverage."

embeddings = HuggingFaceEmbeddings(model_name="BAAI/bge-small-en-v1.5")

hypo_embedding = embeddings.embed_query(hypothetical_answer)

In [25]:
retrieved_docs = vector_store.similarity_search_by_vector(hypo_embedding)

for doc in retrieved_docs:
    print(doc.page_content)
    print("------------|")

National Insurance Co. Ltd.
National Parivar Mediclaim Plus Policy
Premises No. 18-0374, Plot no. CBD-81,
Page 6 of 25
UIN: NICHLIP25039V032425
New Town, Kolkata 700156
as shown in the Table of Benefits. The female Insured Person should have been continuously covered for at least 24 months before
availing this benefit.
The New Born Baby shall be automatically covered from birth under the Sum Insured available to the mother during the
corresponding Policy Period, for up to 3 months of age. On attaining 3 months of age, the New Born Baby shall be covered only if
specifically included in the Policy mid-term and requisite premium paid to the Company.
Cover
Maternity Expenses means;
a) Medical treatment expenses traceable to childbirth (including complicated deliveries and caesarean sections incurred during
Hospitalization);
b) Expenses towards lawful medical termination of pregnancy during the Policy Period.
------------|
for any other critical illness during the policy year.
2 On renewal,

In [41]:
from langchain_google_genai import ChatGoogleGenerativeAI
from langchain.prompts import PromptTemplate
from langchain_core.runnables import RunnablePassthrough
from langchain_core.output_parsers import StrOutputParser
from utilities.text_utils import format_docs
from prompts import BASIC_PROMPT

def answer_using_hyde(file_hash, query):
    # Load vector store and LLM
    vector_store = FAISS.load_local(
        f"vector_store/{file_hash}", embeddings, allow_dangerous_deserialization=True
    )

    llm = ChatGoogleGenerativeAI(
        model="gemini-2.0-flash",
        temperature=0,
        max_tokens=None,
        timeout=None,
        max_retries=2,
    )

    # --- HyDe step: Generate hypothetical answer ---
    hyde_prompt = f"""You are given a user query. Generate a concise, factual, and contextually relevant hypothetical answer that directly addresses the query. 
    This answer will be used for semantic search, so it should resemble the kind of language and format typically found in documents or knowledge bases.

    Focus only on the core information asked in the query. Do not speculate or include unrelated details.

    Query: {query}
    Hypothetical Answer:"""

    try:
        hypo_answer = llm.predict(hyde_prompt).strip()
        if not hypo_answer:
            print(f"Empty hypothetical answer for query: {query}")
            answer = "Could not generate a relevant answer."
            return answer

        # --- Embed the hypothetical answer for retrieval ---
        print(hypo_answer)
        hypo_embedding = embeddings.embed_query(hypo_answer)


        docs = vector_store.similarity_search_by_vector(hypo_embedding, k=5)

        for doc in docs:
            print(doc.page_content)

        # --- Build and run RAG chain ---
        prompt = PromptTemplate.from_template(BASIC_PROMPT)
        rag_chain = (
            {"context": RunnablePassthrough(), "question": RunnablePassthrough()}
            | prompt
            | llm
            | StrOutputParser()
        )

        answer = rag_chain.invoke({"context": format_docs(docs), "question": query})
    except Exception as e:
        print(f"Error processing query '{query}': {e}")
        answer = "Error occurred while processing the query."

    return answer


In [42]:
answer_using_hyde("042f627c5d8f619cf62cc21f864b08dfd59059d0b9aab805d132e0014489d625", "What is the grace period for premium payment under the National Parivar Mediclaim Plus Policy?")

The grace period for premium payment under the National Parivar Mediclaim Plus Policy is 30 days.
break.
National Insurance Co. Ltd.
National Parivar Mediclaim Plus Policy
Premises No. 18-0374, Plot no. CBD-81,
Page 4 of 25
UIN: NICHLIP25039V032425
New Town, Kolkata 700156
3 BENEFITS COVERED UNDER THE POLICY
3.1COVERAGE
3.1.1 In-patient Treatment
The Company shall indemnify the medical expenses for:
i. Room charges and intensive care unit charges (including diet charges, nursing care by qualified nurse, RMO charges,
administration charges for IV fluids/blood transfusion/injection), subject to limit as per Section 3.1.1.1
ii. Medical practitioner(s)
iii. Anaesthesia, blood, oxygen, operation theatre charges, surgical appliances
iv. Medicines and drugs
V. Diagnostic procedures
vi. Prosthetics and other devices or equipment if implanted internally during a surgical procedure.
vii. Dental treatment, necessitated due to an injury
viii. Plastic surgery, necessitated due to disease or injury


'Break in policy means the period of gap that occurs when the premium due for renewal is not paid on or before the premium renewal date or grace period.'

In [28]:
import os
from google import genai

def get_document_summary(file_path):
    try:
        with open(file_path, "rb") as f:
            pdf_bytes = f.read()

        client = genai.Client(api_key=os.getenv("GOOGLE_API_KEY"))
        pdf_file = client.files.upload(file=pdf_bytes)
        response = client.models.generate_content(
            model="gemini-2.0-flash",
            contents=["summarize the document", pdf_file]
        )
        print(response)
        summary = response.text
    except Exception as e:
        print(f"Error generating summary: {e}")
        summary = f"Could not generate summary. {e}"

    return summary


In [29]:
abs_path = os.path.abspath("docs/042f627c5d8f619cf62cc21f864b08dfd59059d0b9aab805d132e0014489d625.pdf")
summary = get_document_summary(abs_path)


Error generating summary: b'%PDF-1.7\r\n%\xb5\xb5\xb5\xb5\r\n1 0 obj\r\n<</Type/Catalog/Pages 2 0 R/Lang(en-IN) /StructTreeRoot 112 0 R/MarkInfo<</Marked true>>/Metadata 3575 0 R/ViewerPreferences 3576 0 R>>\r\nendobj\r\n2 0 obj\r\n<</Type/Pages/Count 25/Kids[ 3 0 R 27 0 R 33 0 R 37 0 R 39 0 R 41 0 R 57 0 R 59 0 R 61 0 R 63 0 R 65 0 R 67 0 R 69 0 R 71 0 R 75 0 R 82 0 R 84 0 R 93 0 R 95 0 R 97 0 R 99 0 R 101 0 R 103 0 R 105 0 R 107 0 R] >>\r\nendobj\r\n3 0 obj\r\n<</Type/Page/Parent 2 0 R/Resources<</Font<</F1 5 0 R/F2 9 0 R/F3 11 0 R/F4 14 0 R/F5 16 0 R/F6 21 0 R/F7 23 0 R/F8 25 0 R>>/ExtGState<</GS7 7 0 R/GS8 8 0 R>>/XObject<</Image13 13 0 R>>/ProcSet[/PDF/Text/ImageB/ImageC/ImageI] >>/MediaBox[ 0 0 595.32 841.92] /Contents 4 0 R/Group<</Type/Group/S/Transparency/CS/DeviceRGB>>/Tabs/S/StructParents 0>>\r\nendobj\r\n4 0 obj\r\n<</Filter/FlateDecode/Length 7753>>\r\nstream\r\nx\x9c\xc5=ks\xdc6\x92\xdf]\xe5\xff\xc0\x8f3[\x16E\x82\xe0k7\xa5*Ivb\xdf\xc5Y\xdd\xda\xb9\xad\xad\xec~\x18\x8fG\x

In [30]:
summary

'Could not generate summary. b\'%PDF-1.7\\r\\n%\\xb5\\xb5\\xb5\\xb5\\r\\n1 0 obj\\r\\n<</Type/Catalog/Pages 2 0 R/Lang(en-IN) /StructTreeRoot 112 0 R/MarkInfo<</Marked true>>/Metadata 3575 0 R/ViewerPreferences 3576 0 R>>\\r\\nendobj\\r\\n2 0 obj\\r\\n<</Type/Pages/Count 25/Kids[ 3 0 R 27 0 R 33 0 R 37 0 R 39 0 R 41 0 R 57 0 R 59 0 R 61 0 R 63 0 R 65 0 R 67 0 R 69 0 R 71 0 R 75 0 R 82 0 R 84 0 R 93 0 R 95 0 R 97 0 R 99 0 R 101 0 R 103 0 R 105 0 R 107 0 R] >>\\r\\nendobj\\r\\n3 0 obj\\r\\n<</Type/Page/Parent 2 0 R/Resources<</Font<</F1 5 0 R/F2 9 0 R/F3 11 0 R/F4 14 0 R/F5 16 0 R/F6 21 0 R/F7 23 0 R/F8 25 0 R>>/ExtGState<</GS7 7 0 R/GS8 8 0 R>>/XObject<</Image13 13 0 R>>/ProcSet[/PDF/Text/ImageB/ImageC/ImageI] >>/MediaBox[ 0 0 595.32 841.92] /Contents 4 0 R/Group<</Type/Group/S/Transparency/CS/DeviceRGB>>/Tabs/S/StructParents 0>>\\r\\nendobj\\r\\n4 0 obj\\r\\n<</Filter/FlateDecode/Length 7753>>\\r\\nstream\\r\\nx\\x9c\\xc5=ks\\xdc6\\x92\\xdf]\\xe5\\xff\\xc0\\x8f3[\\x16E\\x82\\xe0k7\\xa5